# Citi Bike Data
New York's Citi Bikes make up the largest bike share program in the country. It began three years ago in May 2013 and currently consists of a fleet of 6,000 bikes, which the city plans to double by next year. Citi Bike's data is [publicly available](https://www.citibikenyc.com/system-data) and I was curious what I could extract from it. At first I wanted to examine the tourists' use of the Citi Bikes but couldn't find much that was interesting or other datasets that would make my findings more useful. So I pivoted and decided to look at how residents (including the permanent residents *and* tourists) utilized the bike stations in their area.

I looked at data from April 2015-March 2016 and it included over a million recorded trips. I narrowed data to only trips that started in the morning (between 5am-11:59:59am) when most people would be commuting so that I could reduce the trips of people returning from work in the evening (I considered this duplicate data and not representative of true departures from people's local bike stations). This cut the data down to just over 800k records.



In [1]:
import pandas as pd
import numpy as np
from numpy import pi
import os
from datetime import datetime
import time
import urllib.request, json

In [2]:
data_list = os.listdir('./data')
df = pd.read_csv('./data/'+data_list[2]) #first item was a dotfile
for x in data_list[3:]:
    df2 = pd.read_csv('./data/'+x)
    df = pd.concat([df, df2])
        
df.head()

tripduration          starttime           stoptime  start station id  \
0           241  4/1/2015 00:00:23  4/1/2015 00:04:25               494   
1           578  4/1/2015 00:00:52  4/1/2015 00:10:31                82   
2           484  4/1/2015 00:01:28  4/1/2015 00:09:33               223   
3          1144  4/1/2015 00:01:31  4/1/2015 00:20:36               393   
4          1023  4/1/2015 00:01:36  4/1/2015 00:18:40               212   

        start station name  start station latitude  start station longitude  \
0          W 26 St & 8 Ave               40.747348               -73.997236   
1   St James Pl & Pearl St               40.711174               -74.000165   
2          W 13 St & 7 Ave               40.737815               -73.999947   
3        E 5 St & Avenue C               40.722992               -73.979955   
4  W 16 St & The High Line               40.743349               -74.006818   

   end station id       end station name  end station latitude  \
0             489       10 Ave & W 28 St             40.750664   
1            2008  Little West St & 1 Pl             40.705693   
2             445     E 10 St & Avenue A             40.727408   
3             393      E 5 St & Avenue C             40.722992   
4             438    St Marks Pl & 1 Ave             40.727791   

   end station longitude  bikeid    usertype  birth year  gender  
0             -74.001768   15510  Subscriber        1992       2  
1             -74.016777   15014  Subscriber        1982       1  
2             -73.981420   20881  Subscriber        1986       2  
3             -73.979955   20295  Subscriber        1977       2  
4             -73.985649   19871  Subscriber        1979       1

In [5]:
def convert_datetime(dt):
    try: 
        t = datetime.strptime(dt,'%m/%d/%Y %H:%M:%S')
    except:
        t = datetime.strptime(dt,'%m/%d/%Y %H:%M')
    d = t.timetuple()
    return time.mktime(d)

def get_hour_of_day(timestamp):
    return datetime.utcfromtimestamp(timestamp).hour


In [6]:
df['start datetime'] = df.starttime.apply(convert_datetime)
df['start hour'] = df['start datetime'].apply(get_hour_of_day)
df['stop datetime'] = df.stoptime.apply(convert_datetime)
df['stop hour'] = df['stop datetime'].apply(get_hour_of_day)

In [64]:
#Only want morning times to reduce data of commuters returning from work (ie those coming from non residential areas)

df = df.loc[(5 <= df['start hour']) & (df['start hour'] < 12)] #only want morning users (when leaving place of residence)
#df = df.loc[df['usertype'] != 'Subscriber'] #only want tourists (non-commuters)

In [8]:
df.reset_index(drop=True, inplace=True)

If you are going to use this code, get an api key from google maps and put it in the string below

In [66]:
key=''

## IMPORTANT

Uncomment the below if starting this file fresh, then comment it back out when done getting zip codes so that you don't accidentally reset the memoization. I really should save the dictionaries keys and values to a separate file but I did most of this project in one sitting and didn't need it (there are something like 500 bike stations and google gives 2500 api calls/day).

In [67]:
#geo_memo = {}

In [68]:
def get_zip(address):
    address = address.replace('&', 'and')
    #print(address)
    address += ' NY'
    pre = 'https://maps.googleapis.com/maps/api/geocode/json?address='
    post='&key='+key
    if address in geo_memo:
        return geo_memo[address]
    else:
        a = '+'.join(address.split(' '))
        a = '+'.join(a.split('\xa0'))
        url = pre+a+post
        #print(a,url)
        with urllib.request.urlopen(url) as open_url:
            s = open_url.read().decode('utf-8')        
        data = json.loads(s)
        for x in data['results'][0]['address_components']:
            if x['types'][0] == "postal_code":
                loc = x['short_name']
                break
        try:
            loc = int(loc)
        except: #if zip not found because its a route, take the lat/lng and get val from that
            lat=str(data['results'][0]['geometry']['location']['lat'])
            lng=str(data['results'][0]['geometry']['location']['lng'])
            pre = 'https://maps.googleapis.com/maps/api/geocode/json?latlng='
            url = pre+lat+','+lng+post
            with urllib.request.urlopen(url) as open_url:
                s = open_url.read().decode('utf-8')
            data = json.loads(s)
            for x in data['results'][0]['address_components']:
                if x['types'][0] == "postal_code":
                    loc = x['short_name']
                    break
            loc = int(loc)
        geo_memo[address] = loc
        return loc


In [69]:
df['start zipcode'] = df['start station name'].apply(get_zip)
df['end zipcode'] = df['end station name'].apply(get_zip)

#something got screwed up in my memoization, some values were ints, others strings
#only had a limited number of api calls per day so did this instead
df['start zipcode'] = df['start zipcode'].apply(lambda x:int(x))
df['end zipcode'] = df['end zipcode'].apply(lambda x:int(x))

/Users/kenn/anaconda/envs/py35/lib/python3.5/site-packages/ipykernel/__main__.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  if __name__ == '__main__':
/Users/kenn/anaconda/envs/py35/lib/python3.5/site-packages/ipykernel/__main__.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  from ipykernel import kernelapp as app
/Users/kenn/anaconda/envs/py35/lib/python3.5/site-packages/ipykernel/__main__.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = va

In [70]:
df.head(1)

tripduration          starttime           stoptime  start station id  \
101           274  4/1/2015 01:02:25  4/1/2015 01:07:00               401   

          start station name  start station latitude  start station longitude  \
101  Allen St & Rivington St               40.720196               -73.989978   

     end station id   end station name  end station latitude     ...       \
101             301  E 2 St & Avenue B             40.722174     ...        

     bikeid    usertype birth year  gender  start datetime  start hour  \
101   17864  Subscriber       1978       1      1427864545           5   

     stop datetime  stop hour  start zipcode  end zipcode  
101     1427864820          5          10002        10009  

[1 rows x 21 columns]

I have narrowed the data down to trips between the hours of 5am-11:59:59am (when people would be leaving their place of residence so that it reduces the overlap with when they might return) and added the zip codes. 

In [71]:
import bokeh
from bokeh.charts import Bar, show, ColumnDataSource
from bokeh.plotting import figure
from bokeh.models import HoverTool, LinearAxis, Range1d
from bokeh.models.ranges import FactorRange
from bokeh.io import output_notebook, output_file, show
from bokeh.charts.attributes import CatAttr

output_notebook()

Loading BokehJS ...

In [72]:
startzip_counts = pd.DataFrame(df['start zipcode'].value_counts())
startzip_counts.rename(columns={'start zipcode':'count'}, inplace=True)
startzip_counts['type'] = 'Start'

endzip_counts = pd.DataFrame(df['end zipcode'].value_counts())
endzip_counts['type'] = 'End'
endzip_counts.rename(columns={'end zipcode':'count'}, inplace=True)

zip_counts = pd.concat([startzip_counts, endzip_counts], axis=0)
zip_counts.head()

count   type
10001  77424  Start
10036  64216  Start
10003  62351  Start
10009  55130  Start
10011  53793  Start

In [73]:
zip_counts.reset_index(drop=False,inplace=True)

In [74]:
zip_counts['index'] = zip_counts['index'].apply(lambda x:str(x))
zip_counts.rename(columns={'index':'zip'}, inplace=True)

In [75]:
zip_counts.head()

zip  count   type
0  10001  77424  Start
1  10036  64216  Start
2  10003  62351  Start
3  10009  55130  Start
4  10011  53793  Start

In [124]:
TOOLS = 'pan,box_zoom,wheel_zoom,crosshair,resize,reset'

p1 = Bar(zip_counts, values='count', label='zip', title="Number of Rides from/to a Station in a Zipcode (Apr 2015-Mar 2016)", 
        width=800,height=450, group='type', tools=[TOOLS, HoverTool(tooltips=[('Zip', "@zip"),('Count', "@height")])],
       legend='top_right', ylabel="# of Rides", color=['#f45666','#5c57f2'])
#p1.x_range = FactorRange(factors=startzip_counts.index.tolist())
output_file('fig1.html')
show(p1)

Here we see the top 10 zip codes for bike rentals:

In [77]:
startzip_counts.head(10)

count   type
10001  77424  Start
10036  64216  Start
10003  62351  Start
10009  55130  Start
10011  53793  Start
10002  47811  Start
10014  39602  Start
10016  39302  Start
10019  37253  Start
10010  32979  Start

And the top 10 destinations:

In [78]:
endzip_counts.head(10)

count type
10019  64411  End
10003  64186  End
10011  51947  End
10016  47238  End
10022  45698  End
10010  44971  End
10001  44930  End
10017  38710  End
10013  36121  End
10036  34652  End

Currently this data is showing just mornings between 5am-11:59:59am which is why the departures and arrivals look so different. Unsurprisingly, when looking at the traffic over the course of the day, both of the top 10s are the same (more commuters use the bikes than tourists and commuters need to return to the same location they started.

In [79]:
pop_data = pd.read_csv('./data/2010+Census+Population+By+Zipcode+(ZCTA).csv')
#pop_data['Zip Code ZCTA'] = pop_data['Zip Code ZCTA'].apply(lambda x:str(x))
pop_data.head()

Zip Code ZCTA  2010 Census Population
0           1001                   16769
1           1002                   29049
2           1003                   10372
3           1005                    5079
4           1007                   14649

In [80]:
z2 = startzip_counts
z2.reset_index(inplace=True,drop=False)
pop_with_bikes = pd.merge(z2, pop_data, how='inner', left_on='index', right_on='Zip Code ZCTA')
pop_with_bikes.head()

index  count   type  Zip Code ZCTA  2010 Census Population
0  10001  77424  Start          10001                   21102
1  10036  64216  Start          10036                   24711
2  10003  62351  Start          10003                   56024
3  10009  55130  Start          10009                   61347
4  10011  53793  Start          10011                   50984

In [81]:
nyc_zip_pops = pop_with_bikes[['Zip Code ZCTA', '2010 Census Population']]
nyc_zip_pops.sort('2010 Census Population', inplace=True, ascending=False)
nyc_zip_pops.reset_index(inplace=True, drop=True)

/Users/kenn/anaconda/envs/py35/lib/python3.5/site-packages/ipykernel/__main__.py:2: FutureWarning: sort(columns=....) is deprecated, use sort_values(by=.....)
  from ipykernel import kernelapp as app
/Users/kenn/anaconda/envs/py35/lib/python3.5/site-packages/pandas/core/frame.py:3167: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  inplace=inplace, kind=kind, na_position=na_position)


In [82]:
nyc_zip_pops.head(10)

Zip Code ZCTA  2010 Census Population
0          11211                   90117
1          11206                   81677
2          10002                   81410
3          11221                   78895
4          11233                   67053
5          11213                   63767
6          10009                   61347
7          10023                   60998
8          10024                   59283
9          10003                   56024

This is interesting. The most populated zip codes aren't the ones with the most bike trips. In fact, the number 1 zip for rides is number 10 in population.

Let's look at

(rides/day)/number stations in zip = rides/station

This might tell us where there excessive rides from a station.

In [83]:
pop_with_bikes.rename(columns={'index':'zip'}, inplace=True)
pop_with_bikes.reset_index(inplace=True)
pop_with_bikes.rename(columns={'index':'rides_rank'}, inplace=True)
pop_with_bikes.drop('type',inplace=True,axis=1)
pop_with_bikes.rides_rank = pop_with_bikes.rides_rank.apply(lambda x:x+1)
pop_with_bikes.drop('Zip Code ZCTA',inplace=True,axis=1)
pop_with_bikes.sort('2010 Census Population', inplace=True, ascending=False)
pop_with_bikes['rides_per_day'] = pop_with_bikes['count']/365

/Users/kenn/anaconda/envs/py35/lib/python3.5/site-packages/ipykernel/__main__.py:7: FutureWarning: sort(columns=....) is deprecated, use sort_values(by=.....)


In [84]:
pop_with_bikes.head(10)

rides_rank    zip  count  2010 Census Population  rides_per_day
22          23  11211   9134                   90117      25.024658
34          35  11206   2393                   81677       6.556164
5            6  10002  47811                   81410     130.989041
41          42  11221    633                   78895       1.734247
42          43  11233    178                   67053       0.487671
43          44  11213    139                   63767       0.380822
3            4  10009  55130                   61347     151.041096
18          19  10023  12284                   60998      33.654795
26          27  10024   5700                   59283      15.616438
2            3  10003  62351                   56024     170.824658

Lets find out how many stations are in each zip code

In [85]:
df3 = df
station_counts = pd.DataFrame(df3.groupby(['start zipcode'])['start station name'].unique().apply(lambda x:len(x)))
station_counts.reset_index(inplace=True, drop=False)
station_counts.rename(columns={'start station name':'station count'}, inplace=True)

In [86]:
station_counts.head()

start zipcode  station count
0          10001             14
1          10002             26
2          10003             21
3          10004              7
4          10005              3

In [87]:
new_df = pd.merge(pop_with_bikes, station_counts, how='left', left_on='zip', right_on='start zipcode')
new_df.drop('start zipcode', inplace=True, axis=1)
new_df['rides_per_day_per_station'] = new_df.rides_per_day/new_df['station count']

In [88]:
new_df.sort('rides_per_day_per_station', ascending=False, inplace=True)
new_df

/Users/kenn/anaconda/envs/py35/lib/python3.5/site-packages/ipykernel/__main__.py:1: FutureWarning: sort(columns=....) is deprecated, use sort_values(by=.....)
  if __name__ == '__main__':


rides_rank    zip  count  2010 Census Population  rides_per_day  \
46          16  10168  15980                       0      43.780822   
33           1  10001  77424                   21102     212.120548   
31           2  10036  64216                   24711     175.934247   
41          22  10282   9506                    4783      26.043836   
36          31  10280   3999                    7853      10.956164   
6            4  10009  55130                   61347     151.041096   
25          10  10010  32979                   31834      90.353425   
12           8  10016  39302                   54183     107.676712   
9            3  10003  62351                   56024     170.824658   
39          11  10018  29107                    5229      79.745205   
14           5  10011  53793                   50984     147.378082   
23           7  10014  39602                   31959     108.498630   
18           9  10019  37253                   42870     102.063014   
32          12  10012  23379                   24090      64.052055   
2            6  10002  47811                   81410     130.989041   
38          18  10007  14629                    6988      40.079452   
40          32  10069   3172                    5199       8.690411   
35          14  10017  17714                   16575      48.531507   
28          13  10013  21681                   27700      59.400000   
26          36  12020   2359                   31192       6.463014   
44          40  10006   1148                    3011       3.145205   
34          21  10038  10885                   20300      29.821918   
37          33  10005   3095                    7135       8.479452   
24          15  10022  16344                   31924      44.778082   
7           19  10023  12284                   60998      33.654795   
43          25  10004   5831                    3089      15.975342   
27          41  12203    778                   29952       2.131507   
19          20  11205  11879                   40366      32.545205   
21          24  11217   7056                   35881      19.331507   
8           27  10024   5700                   59283      15.616438   
22          30  10065   4414                   32270      12.093151   
16          26  10028   5735                   45141      15.712329   
15          29  11238   4878                   49262      13.364384   
17          34  10021   2557                   43631       7.005479   
13          17  11201  15965                   51128      43.739726   
29          38  10075   1924                   26121       5.271233   
0           23  11211   9134                   90117      25.024658   
20          28  11222   5367                   36934      14.704110   
11          39  11216   1823                   54316       4.994521   
30          37  11101   2238                   25484       6.131507   
1           35  11206   2393                   81677       6.556164   
3           42  11221    633                   78895       1.734247   
42          45  11109     77                    3523       0.210959   
5           44  11213    139                   63767       0.380822   
4           43  11233    178                   67053       0.487671   
45          46  12853     59                    1770       0.161644   
10          47  10306     10                   55909       0.027397   

    station count  rides_per_day_per_station  
46              2                  21.890411  
33             14                  15.151468  
31             12                  14.661187  
41              2                  13.021918  
36              1                  10.956164  
6              16                   9.440068  
25             10                   9.035342  
12             13                   8.282824  
9              21                   8.134508  
39             10                   7.974521  
14             19                   7.756741  
23             14              

From this we can see that population can be meaningless in some instances. The number 1 zip code for rides per day per station is a zipcode without any residents, it is a shopping center near grand central.

But we see something else that is interesting. Many of the zip codes toward the bottom, with low daily riders, have large populations. Reasons for this may be beyond the scope of what i'm looking at right now but could be worth looking into in the future (are these wealthier/poorer areas? do more people own bikes here, less business to commute to? or were these just the newest places to get stations?).

In [89]:
new_df['rides_per_day_per_station_per_capita'] = new_df['rides_per_day_per_station']/new_df['2010 Census Population']
#drop the infinite
new_df = new_df.replace([np.inf, -np.inf], np.nan).dropna(subset=['rides_per_day_per_station_per_capita'], how="all")
new_df.sort('rides_per_day_per_station_per_capita', ascending=False, inplace=True)
new_df

/Users/kenn/anaconda/envs/py35/lib/python3.5/site-packages/ipykernel/__main__.py:4: FutureWarning: sort(columns=....) is deprecated, use sort_values(by=.....)


rides_rank    zip  count  2010 Census Population  rides_per_day  \
41          22  10282   9506                    4783      26.043836   
39          11  10018  29107                    5229      79.745205   
36          31  10280   3999                    7853      10.956164   
44          40  10006   1148                    3011       3.145205   
40          32  10069   3172                    5199       8.690411   
43          25  10004   5831                    3089      15.975342   
33           1  10001  77424                   21102     212.120548   
38          18  10007  14629                    6988      40.079452   
31           2  10036  64216                   24711     175.934247   
37          33  10005   3095                    7135       8.479452   
25          10  10010  32979                   31834      90.353425   
35          14  10017  17714                   16575      48.531507   
23           7  10014  39602                   31959     108.498630   
32          12  10012  23379                   24090      64.052055   
6            4  10009  55130                   61347     151.041096   
12           8  10016  39302                   54183     107.676712   
14           5  10011  53793                   50984     147.378082   
34          21  10038  10885                   20300      29.821918   
9            3  10003  62351                   56024     170.824658   
18           9  10019  37253                   42870     102.063014   
28          13  10013  21681                   27700      59.400000   
26          36  12020   2359                   31192       6.463014   
45          46  12853     59                    1770       0.161644   
24          15  10022  16344                   31924      44.778082   
27          41  12203    778                   29952       2.131507   
2            6  10002  47811                   81410     130.989041   
42          45  11109     77                    3523       0.210959   
22          30  10065   4414                   32270      12.093151   
29          38  10075   1924                   26121       5.271233   
21          24  11217   7056                   35881      19.331507   
19          20  11205  11879                   40366      32.545205   
7           19  10023  12284                   60998      33.654795   
16          26  10028   5735                   45141      15.712329   
17          34  10021   2557                   43631       7.005479   
15          29  11238   4878                   49262      13.364384   
8           27  10024   5700                   59283      15.616438   
13          17  11201  15965                   51128      43.739726   
20          28  11222   5367                   36934      14.704110   
30          37  11101   2238                   25484       6.131507   
0           23  11211   9134                   90117      25.024658   
11          39  11216   1823                   54316       4.994521   
1           35  11206   2393                   81677       6.556164   
3           42  11221    633                   78895       1.734247   
5           44  11213    139                   63767       0.380822   
4           43  11233    178                   67053       0.487671   
10          47  10306     10                   55909       0.027397   

    station count  rides_per_day_per_station  \
41              2                  13.021918   
39             10                   7.974521   
36              1                  10.956164   
44              1                   3.145205   
40              2                   4.345205   
43              7                   2.282192   
33             14                  15.151468   
38              9                   4.453272   
31             12                  14.661187   
37              3                   2.826484   
25             10                   9.035342   
35             12                   4.044292   
23             14                   7.7499

In [90]:
new_df['zip'] = new_df['zip'].apply(lambda x:str(x))

In [91]:
bokeh.io.push_notebook()

In [108]:
p = figure(x_range=new_df['zip'].tolist(),plot_width=800, plot_height=450, 
           tools=[TOOLS, HoverTool(tooltips=[('Zip', "@x"),('((Rides/day)/station)/capita', "@height"),('#Stations','@y2')])],
           title="RDSC and # of Stations in a Zipcode (Apr 2015-Mar 2016)")

p.xaxis.axis_label = 'Zip Code'
p.yaxis.axis_label = 'RDSC'

source1 = ColumnDataSource({'x':new_df['zip'], 'y1':new_df['rides_per_day_per_station_per_capita']/2, 'y2':new_df['station count']})
bar_height = new_df['rides_per_day_per_station_per_capita']

p.rect('x','y1', source=source1, width=.9, height=bar_height, color='#f45666', legend='RDSC')
p.circle('x','y2', source=source1, y_range_name='NumStations', color='#5c57f2', legend='# of Stations')

p.y_range = Range1d(0, .003)
p.extra_y_ranges = {"NumStations": Range1d(start=0, end=35)}
p.add_layout(LinearAxis(y_range_name="NumStations", axis_label="# of Stations"), 'right')
p.xaxis.major_label_orientation = pi/4

p.legend.location = "top_right"
output_file('fig2.html')
show(p)

I figured someone might be interested in the same graph as above but with (Rides/day)/capita (RDC) rather than RDSC (in case you wanted to look at many rides and area uses per day, regardless of the number of stations there).

In [109]:
new_df['rides_per_day_per_capita'] = new_df['rides_per_day']/new_df['2010 Census Population']
#drop the infinite
new_df = new_df.replace([np.inf, -np.inf], np.nan).dropna(subset=['rides_per_day_per_capita'], how="all")
new_df.sort('rides_per_day_per_capita', ascending=False, inplace=True)

/Users/kenn/anaconda/envs/py35/lib/python3.5/site-packages/ipykernel/__main__.py:4: FutureWarning: sort(columns=....) is deprecated, use sort_values(by=.....)


In [113]:
p3 = figure(x_range=new_df['zip'].tolist(),plot_width=800, plot_height=450, 
            tools=[TOOLS, HoverTool(tooltips=[('Zip', "@x"),('(Rides/day)/capita', "@height"),('#Stations','@y2')])],
            title="RDC and # of Stations in a Zipcode (Apr 2015-Mar 2016)")

p3.xaxis.axis_label = 'Zip Code'
p3.yaxis.axis_label = 'RDC'

source1 = ColumnDataSource({'x':new_df['zip'], 'y1':new_df['rides_per_day_per_capita']/2, 'y2':new_df['station count']})
bar_height = new_df['rides_per_day_per_capita']

p3.rect('x','y1', source=source1, width=.9, height=bar_height, color='#f45666', legend='RDC')
p3.circle('x','y2', source=source1, y_range_name='NumStations', color='#5c57f2', legend='# of Stations')

p3.y_range = Range1d(0, .016)
p3.extra_y_ranges = {"NumStations": Range1d(start=0, end=35)}
p3.add_layout(LinearAxis(y_range_name="NumStations", axis_label="# of Stations"), 'right')
p3.xaxis.major_label_orientation = pi/4

p3.legend.location = "top_right"
output_file('fig3.html')
show(p3)

These results were more interesting than I expected. We see some areas like 10282 (an area near the WTC) that get a lot of use out of their available bike stations. However, there are other zip codes like 11201 (located in Brooklyn) which has the most stations at 32 and very low RDSC. Comparing this with the earlier data, we see that 11201 isn't even in the top 10 places do depart or arrive at. **So why does it have the most bike stations?** 

We do not have a baseline of what constitutes a surplus or deficit of bikes at a location (it is not possible to obtain that from this data, at least while we don't know how many bikes are at a location to start). Because of this we cannot say that there is a deficit of bikes at 10282. However we can begin using this to examine where bike stations are underutilized, as it appears at 11201. 

Two immediate reactions to these areas come to mind:

1. Either more promotion needs to be done in these areas to get people using the bikes, or
2. Less bikestations are needed in these areas and they can be moved to where true bike deficits occur.

While it would appear that either of these would be good actions to take, it would probably be better to collect even more data first:

1. As stated before, where are the true deficits and surpluses?
2. What other factors might be preventing people from using the bikes in these locations?
    1. Are people wealthy enough that they own bikes?
    2. Do people not have enough disposable income to purchase memberships?
    3. Are people less healthy in these areas?
    4. Are people less likely to know how to ride a bike?
    5. etc.
3. Does each bike station hold the same number of bikes? If so, what is that number, and if not what are the numbers on each station? This is crucial because do we know if the 32 stations in 11201 only hold 1 bike each (it is doubtful but these variables should be accounted for).
    
For now we have found a place to start analyzing the underutilization of Citi Bikes. We know areas where residents use them the most and areas where they use them the least. Even without the above questions answered, NYC Bike Share could still use information like this to redistribute bike stations and see how it balances out the residents' use.